In [1]:
import pandas as pd
import json
from web3 import Web3
from datetime import datetime, timedelta
import time
import sys
import json
from collections import Counter

# Connect to ETH blockchain with infura API key
w3 = Web3(Web3.HTTPProvider('https://mainnet.infura.io/v3/5f0c4998d7544ee1bb3f0dc297a6821c'))

# AAVE V3 ETH Mainnet Market Pool Address
contract_addr = '0x87870Bca3F3fD6335C3F4ce8392D69350B4fA4E2'

# Load ABI
with open("./abi.json") as f:
    pool_abi = json.load(f)
    
# Load Contract
aave_pool_contract = w3.eth.contract(address=contract_addr, abi=pool_abi)

In [2]:
def find_block_by_timestamp(target_timestamp):
    # Start with most recent block
    latest_block = w3.eth.block_number
    earliest_block = 0

    while earliest_block <= latest_block:
        mid_block = (earliest_block + latest_block) // 2
        mid_block_timestamp = w3.eth.get_block(mid_block).timestamp

        if mid_block_timestamp < target_timestamp:
            earliest_block = mid_block + 1
        else:
            latest_block = mid_block - 1
            
        if latest_block - earliest_block == 1:
            if abs(web3.eth.get_block(earliest_block).timestamp - target_timestamp) <= \
               abs(web3.eth.get_block(latest_block).timestamp - target_timestamp):
                return earliest_block
            else:
                return latest_block

    return earliest_block

# Find the block number three months from now
# Get block number of 3 months ago with binary search
current_time = datetime.now()
three_months_prior = current_time - timedelta(days=90)
three_months_prior_timestamp = int(three_months_prior.timestamp())

three_months_ago_block = find_block_by_timestamp(three_months_prior_timestamp)

In [3]:
# Helper to convert block number to readable timestamp string
def get_block_timestamp(block_num):
    block = w3.eth.get_block(block_num)
    timestamp = block.timestamp
    
    return datetime.utcfromtimestamp(timestamp).strftime('%Y-%m-%d %H:%M:%S')

# Catch withdrawl events from 3 months ago block to latest block
supplies = aave_pool_contract.events.Supply().get_logs(fromBlock=three_months_ago_block,
                                                       toBlock='latest',
                                                       argument_filters={'reserve': '0xae78736Cd615f374D3085123A210448E74Fc6393'})

supplies
# Convert Transactions into ordinary dict format
supply_list = [
    {
        'Reserve': event['args']['reserve'],
        'User (Wallet Address)': event['args']['user'],
        'Amount (Wei)': event['args']['amount'],
        'Amount (rETH)': event['args']['amount']/10**18,
        'Timestamp': get_block_timestamp(event['blockNumber']),
        'LogIndex': event['logIndex'],
        'TransactionIndex': event['transactionIndex'],
        'TransactionHash': event['transactionHash'].hex(),
        'BlockHash': event['blockHash'].hex(),
        'BlockNumber': event['blockNumber']
    }
    for event in supplies
]

# Push withdrawls into dataframe
recent_supplies = pd.DataFrame(supply_list)
recent_supplies['Timestamp'] = pd.to_datetime(recent_supplies['Timestamp'])
recent_supplies

Reserve  \
0    0xae78736Cd615f374D3085123A210448E74Fc6393   
1    0xae78736Cd615f374D3085123A210448E74Fc6393   
2    0xae78736Cd615f374D3085123A210448E74Fc6393   
3    0xae78736Cd615f374D3085123A210448E74Fc6393   
4    0xae78736Cd615f374D3085123A210448E74Fc6393   
..                                          ...   
372  0xae78736Cd615f374D3085123A210448E74Fc6393   
373  0xae78736Cd615f374D3085123A210448E74Fc6393   
374  0xae78736Cd615f374D3085123A210448E74Fc6393   
375  0xae78736Cd615f374D3085123A210448E74Fc6393   
376  0xae78736Cd615f374D3085123A210448E74Fc6393   

                          User (Wallet Address)           Amount (Wei)  \
0    0x0418656Fdf3646968489b8e6aF6C25562803c69D  167090179062388224328   
1    0x4984D35DA85DC841Ae865BF1e39CDA5f1A193Ad8   11247183906907951696   
2    0x4984D35DA85DC841Ae865BF1e39CDA5f1A193Ad8   11938715252405077957   
3    0xADC0A53095A0af87F3aa29FE0715B5c28016364e   10800006511311161204   
4    0x1D9e9719C793B5A4a30Ec47816AF4B531d4f9D09   20165508823083661753   
..                                          ...                    ...   
372  0xDCE7d721aCf944CeE5B8A9A810CcF336CF9c429A    3459295883063065421   
373  0x2d9B182d340A9189457e83d6034cca98Fc81cc6a   97677568611203062938   
374  0x2d9B182d340A9189457e83d6034cca98Fc81cc6a   61030919479260508967   
375  0x03D630d683BcB93608722EC3878f310905e54865   55000000000000000000   
376  0x03D630d683BcB93608722EC3878f310905e54865   49270552585722202900   

     Amount (rETH)           Timestamp  LogIndex  TransactionIndex  \
0       167.090179 2023-11-15 15:31:23       220                82   
1        11.247184 2023-11-16 07:28:35       308               144   
2        11.938715 2023-11-16 07:32:11       161               138   
3        10.800007 2023-11-16 07:33:59       286               179   
4        20.165509 2023-11-16 11:18:47       292               114   
..             ...                 ...       ...               ...   
372       3.459296 2024-02-11 20:42:35       127               100   
373      97.677569 2024-02-11 22:08:59       549                63   
374      61.030919 2024-02-11 22:37:59       250                96   
375      55.000000 2024-02-12 10:28:11        58                42   
376      49.270553 2024-02-12 11:00:23       118                84   

                                       TransactionHash  \
0    0x2377755ca5f4ebc05bf14eeb923d9a18cba0485d832c...   
1    0xbb043d6302cb5d36a4848a94e636fb977b8ffd5d6754...   
2    0xfdaaa26e1183e4790962e346c1e1d4a322ead27b1fd5...   
3    0x549dcf1e3a46bbde3c1389b090b41f26ab6497fd3195...   
4    0x58f378836d92af1c4529ef18b25d4bd01393659eb7e8...   
..                                                 ...   
372  0x58ab8f894c89e0617ad2a770dc999aa27ee465200058...   
373  0x66af0c46bd4fec3a8e21bab7e6b5736de77374119d94...   
374  0xcbd34245b6f82a6c7d1d9f851908a28c8a88937bf8f2...   
375  0x21b2231334b7c370d937f41e5e83a12510eb7ed5a677...   
376  0x22c3df2b161262ef751bd2fecc557e9156cdb6c3fbf1...   

                                             BlockHash  BlockNumber  
0    0xc77324b32c0d304b5b00a64e504e2d415b7525791583...     18578195  
1    0x65ed9ae058db006c17bd6070213b853feca67e335e81...     18582955  
2    0x2356773f8caa376491dbb6f8f55b097bfc7c505b45a5...     18582973  
3    0xd98ad14ba852af5e8e44e7dd8d3bce01b81b23df4729...     18582982  
4    0x9becaca9702baa4bf2b3671b47f0d30561d7e160b304...     18584100  
..                                                 ...          ...  
372  0x0765d934c5e38ccf808eb479201be9148f2e509cd104...     19207263  
373  0x0a7668d95493fdc16c5334c9128d6a4b3152c5333d39...     19207689  
374  0x016052455875a314cb9148cef7ed721d311344287ccb...     19207834  
375  0x750fc3aef799eae80e5b58de4d3782b33a170064602a...     19211350  
376  0x7028f9a65d55097d833fcfcc0099a3bc2adf936ab9ed...     19211510  

[377 rows x 10 columns]

In [4]:
# Get all wallet addresses and block number for recent suppliers as list
recent_suppliers_tup = [(row['User (Wallet Address)'], row['BlockNumber']) for index, row in recent_supplies.iterrows()]

# In case of duplicates, only retain oldest block
min_block_numbers = {}

for address, block_number in recent_suppliers_tup:
    if address in min_block_numbers:
        if block_number < min_block_numbers[address]:
            min_block_numbers[address] = block_number
    else:
        min_block_numbers[address] = block_number
        
recent_suppliers_tup = list(min_block_numbers.items())

In [9]:
def fetch_logs(user_address_filter, target_block, aave_pool_contract, event_name, block_step = 100000):
    """
    Fetches logs for transactions filtered by user address and event type, from the latest block down to a target block.

    Parameters:
    - user_address_filter: The user wallet address to filter the logs.
    - target_block: The block number to stop fetching logs at.
    - aave_pool_contract: The contract object to fetch logs from.
    - event_name: The name of the event to fetch {'Borrow', 'Repay', 'Withdraw', 'FlashLoan'}
    - block_step: The number of blocks to step back in each iteration (default is 100000).

    Returns:
    - A an array of formatted logs.
    """
    print(f'For User: {user_address_filter}\nFrom Block: {target_block}')

    # Dynamic print
    print(f'Fetching {event_name} events', end='')
    sys.stdout.flush()

    # Variables for looping
    logged_results = []
    target_log_count = float('inf')
    current_block = w3.eth.block_number    # Latest Block Number

    # Time
    start = time.time()

    # Loop counter
    iter_count = 0

    # Loop until target number reached or at first block
    while (len(logged_results) < target_log_count and current_block > target_block):
        print('.', end='')

        from_block = max(current_block - block_step, target_block)

        try:
            # Access event
            event = getattr(aave_pool_contract.events, event_name)()
            
            # Fetch logs for the current block
            if (event_name == 'FlashLoan'):
                current_logs = event.get_logs(
                    fromBlock=from_block,
                    toBlock=current_block,
                    argument_filters={'initiator': user_address_filter}
                )
            else:
                current_logs = event.get_logs(
                    fromBlock=from_block,
                    toBlock=current_block,
                    argument_filters={'user': user_address_filter}
                )

            # Format event logs
            for event in current_logs:
                formatted_log = format_event_log(event, event_name)

                # Add to aggregate log list
                logged_results.append(formatted_log)

            # Decrement block number
            current_block = from_block - 1

        except Exception as e:
            # Print exception and block number and break
            print(f"\nError fetching logs for block {current_block}: {e}")
            break

        # Increment iter
        iter_count += 1

    # Print time
    print('\nFetching complete.')
    print(f'Time Elapsed: {time.time() - start}\n')

    # Trim list
    if len(logged_results) > target_log_count:
           logged_results = logged_results[-target_log_count:]

    # Return logged results
    return logged_results

def format_event_log(event, event_name):
    """
    Formats the log of an event based on its type.

    Parameters:
    - event: The event log to format.
    - event_name: The name of the event.

    Returns:
    - A dictionary containing formatted log attributes.
    """
    
    # Format common attrs
    log = {
        'Transaction Hash': event['transactionHash'].hex(),
        'Address': event['address'],
        'Block Hash': event['blockHash'].hex(),
        'Block Number': event['blockNumber'],
        'Timestamp': get_block_timestamp(event['blockNumber']),
    }
    
    # if else tree for event specific attrs
    if event_name == 'Withdraw':
        log.update({
            'Reserve': event['args']['reserve'],
            'User': event['args']['user'],
            'To': event['args']['to'],
            'Amount': event['args']['amount']
        })
        
    elif event_name == 'Borrow':
        log.update({
            'Reserve': event['args']['reserve'],
            'On Behalf Of': event['args']['onBehalfOf'],
            'User': event['args']['user'],
            'Amount': event['args']['amount'],
            'Borrow Rate': event['args']['borrowRate']
        })
        
    elif event_name == 'Repay':
        log.update({
            'Reserve': event['args']['reserve'],
            'User': event['args']['user'],
            'Repayer': event['args']['repayer'],
            'Amount': event['args']['amount'],
            'useAtokens': str(event['args']['useATokens']),
            
        })
        
    elif event_name == 'FlashLoan':
        log.update({
            'Target': event['args']['target'],
            'Asset': event['args']['asset'],
            'Referral Code': str(event['args']['referralCode']),
            'Initiator': event['args']['initiator'],
            'Amount': event['args']['amount'],
            'Premium': event['args']['premium']
        })
    
    return log

In [10]:
event_types = ['Withdraw', 'Borrow', 'Repay', 'FlashLoan']
recentUser_logs = {}

# Loop recent suppliers
for user, block in recent_suppliers_tup:  
    
    # Create sub-dicts for user not already in list
    if user not in recentUser_logs:
        recentUser_logs[user] = {}
    
    
    # Loop event types
    for event_type in event_types:
        # Fetch logs
        logs = fetch_logs(user, block, aave_pool_contract, event_type, 250000)
        
        if event_type not in recentUser_logs[user]:
            recentUser_logs[user][event_type] = {}
            
        # Store fetched logs
        for log in logs:
            # Timestamp
            timestamp = log['Timestamp']
            
            # Init event array in case of multiple events in same block
            if timestamp not in recentUser_logs[user][event_type]:
                recentUser_logs[user][event_type][timestamp] = []
                
            recentUser_logs[user][event_type][timestamp].append(log)
            

For User: 0x0418656Fdf3646968489b8e6aF6C25562803c69D
From Block: 18578195
Fetching Withdraw events...
Fetching complete.
Time Elapsed: 0.17328357696533203

For User: 0x0418656Fdf3646968489b8e6aF6C25562803c69D
From Block: 18578195
Fetching Borrow events...
Fetching complete.
Time Elapsed: 20.618124961853027

For User: 0x0418656Fdf3646968489b8e6aF6C25562803c69D
From Block: 18578195
Fetching Repay events...
Fetching complete.
Time Elapsed: 0.18332409858703613

For User: 0x0418656Fdf3646968489b8e6aF6C25562803c69D
From Block: 18578195
Fetching FlashLoan events...
Fetching complete.
Time Elapsed: 3.361640453338623

For User: 0x4984D35DA85DC841Ae865BF1e39CDA5f1A193Ad8
From Block: 18582955
Fetching Withdraw events...
Fetching complete.
Time Elapsed: 0.11662960052490234

For User: 0x4984D35DA85DC841Ae865BF1e39CDA5f1A193Ad8
From Block: 18582955
Fetching Borrow events...
Fetching complete.
Time Elapsed: 21.362464904785156

For User: 0x4984D35DA85DC841Ae865BF1e39CDA5f1A193Ad8
From Block: 18582955


Fetching Borrow events...
Fetching complete.
Time Elapsed: 19.6487238407135

For User: 0x9Ca458D4E33377E59D140A58Fe37b3417DE93042
From Block: 18600953
Fetching Repay events...
Fetching complete.
Time Elapsed: 0.3438754081726074

For User: 0x9Ca458D4E33377E59D140A58Fe37b3417DE93042
From Block: 18600953
Fetching FlashLoan events...
Fetching complete.
Time Elapsed: 2.952688217163086

For User: 0x33333aea097c193e66081E930c33020272b33333
From Block: 18601115
Fetching Withdraw events...
Fetching complete.
Time Elapsed: 5.905621528625488

For User: 0x33333aea097c193e66081E930c33020272b33333
From Block: 18601115
Fetching Borrow events...
Fetching complete.
Time Elapsed: 31.12976574897766

For User: 0x33333aea097c193e66081E930c33020272b33333
From Block: 18601115
Fetching Repay events...
Fetching complete.
Time Elapsed: 5.7764503955841064

For User: 0x33333aea097c193e66081E930c33020272b33333
From Block: 18601115
Fetching FlashLoan events...
Fetching complete.
Time Elapsed: 3.1117911338806152

Fo

Fetching FlashLoan events...
Fetching complete.
Time Elapsed: 3.1293373107910156

For User: 0x8154322E396db9a428201a906EF1Fa38F5A52C09
From Block: 18625255
Fetching Withdraw events...
Fetching complete.
Time Elapsed: 0.17229151725769043

For User: 0x8154322E396db9a428201a906EF1Fa38F5A52C09
From Block: 18625255
Fetching Borrow events...
Fetching complete.
Time Elapsed: 19.941040754318237

For User: 0x8154322E396db9a428201a906EF1Fa38F5A52C09
From Block: 18625255
Fetching Repay events...
Fetching complete.
Time Elapsed: 0.17340087890625

For User: 0x8154322E396db9a428201a906EF1Fa38F5A52C09
From Block: 18625255
Fetching FlashLoan events...
Fetching complete.
Time Elapsed: 2.949112892150879

For User: 0x0F2A605E9590b024fFD7dE3575aF73238632eFd7
From Block: 18628742
Fetching Withdraw events...
Fetching complete.
Time Elapsed: 0.10634350776672363

For User: 0x0F2A605E9590b024fFD7dE3575aF73238632eFd7
From Block: 18628742
Fetching Borrow events...
Fetching complete.
Time Elapsed: 18.399548768997

Fetching Borrow events...
Fetching complete.
Time Elapsed: 18.476060390472412

For User: 0x5A96D78d63d4f3482B2c2d96915350082036d8C5
From Block: 18664870
Fetching Repay events...
Fetching complete.
Time Elapsed: 0.14123845100402832

For User: 0x5A96D78d63d4f3482B2c2d96915350082036d8C5
From Block: 18664870
Fetching FlashLoan events...
Fetching complete.
Time Elapsed: 2.670964241027832

For User: 0x2b86D62eEbc50615275743F278be7E4c897aAEA2
From Block: 18667740
Fetching Withdraw events...
Fetching complete.
Time Elapsed: 0.17179155349731445

For User: 0x2b86D62eEbc50615275743F278be7E4c897aAEA2
From Block: 18667740
Fetching Borrow events...
Fetching complete.
Time Elapsed: 18.619234323501587

For User: 0x2b86D62eEbc50615275743F278be7E4c897aAEA2
From Block: 18667740
Fetching Repay events...
Fetching complete.
Time Elapsed: 0.2203841209411621

For User: 0x2b86D62eEbc50615275743F278be7E4c897aAEA2
From Block: 18667740
Fetching FlashLoan events...
Fetching complete.
Time Elapsed: 2.70278215408325

Fetching FlashLoan events...
Fetching complete.
Time Elapsed: 2.970123767852783

For User: 0x2338069DBE58617e8302574aef2dd3fb8d488f4F
From Block: 18699653
Fetching Withdraw events...
Fetching complete.
Time Elapsed: 0.07810783386230469

For User: 0x2338069DBE58617e8302574aef2dd3fb8d488f4F
From Block: 18699653
Fetching Borrow events...
Fetching complete.
Time Elapsed: 22.132429122924805

For User: 0x2338069DBE58617e8302574aef2dd3fb8d488f4F
From Block: 18699653
Fetching Repay events...
Fetching complete.
Time Elapsed: 0.07904314994812012

For User: 0x2338069DBE58617e8302574aef2dd3fb8d488f4F
From Block: 18699653
Fetching FlashLoan events...
Fetching complete.
Time Elapsed: 4.027275323867798

For User: 0x15Bc68465d04a31D37E9f8DfE980c145D6b397AF
From Block: 18704712
Fetching Withdraw events...
Fetching complete.
Time Elapsed: 0.14838814735412598

For User: 0x15Bc68465d04a31D37E9f8DfE980c145D6b397AF
From Block: 18704712
Fetching Borrow events...
Fetching complete.
Time Elapsed: 20.1256270408

...

Fetching FlashLoan events..
Fetching complete.
Time Elapsed: 1.7028727531433105

For User: 0x8Fe3e0BC5C1AF0b871B40F043bB0F09E9ACDda3f
From Block: 18889845
Fetching Withdraw events..
Fetching complete.
Time Elapsed: 0.1250619888305664

For User: 0x8Fe3e0BC5C1AF0b871B40F043bB0F09E9ACDda3f
From Block: 18889845
Fetching Borrow events..
Fetching complete.
Time Elapsed: 11.872038841247559

For User: 0x8Fe3e0BC5C1AF0b871B40F043bB0F09E9ACDda3f
From Block: 18889845
Fetching Repay events..
Fetching complete.
Time Elapsed: 0.09020066261291504

For User: 0x8Fe3e0BC5C1AF0b871B40F043bB0F09E9ACDda3f
From Block: 18889845
Fetching FlashLoan events..
Fetching complete.
Time Elapsed: 1.8741545677185059

For User: 0x699d0F798914f19837e05abb62afcC2698726E8C
From Block: 18891785
Fetching Withdraw events..
Fetching complete.
Time Elapsed: 0.09549665451049805

For User: 0x699d0F798914f19837e05abb62afcC2698726E8C
From Block: 18891785
Fetching Borrow events..
Fetching complete.
Time Elapsed: 11.84191346168518



Fetching Borrow events..
Fetching complete.
Time Elapsed: 9.14017629623413

For User: 0x61C00B460b320935aAe718C0Ceb5d864c4864846
From Block: 18964609
Fetching Repay events..
Fetching complete.
Time Elapsed: 0.11277961730957031

For User: 0x61C00B460b320935aAe718C0Ceb5d864c4864846
From Block: 18964609
Fetching FlashLoan events..
Fetching complete.
Time Elapsed: 1.590573787689209

For User: 0x81153a7A0A3ee058F8Ce28FfF298440726499c7f
From Block: 18965976
Fetching Withdraw events.
Fetching complete.
Time Elapsed: 0.03170418739318848

For User: 0x81153a7A0A3ee058F8Ce28FfF298440726499c7f
From Block: 18965976
Fetching Borrow events.
Fetching complete.
Time Elapsed: 10.330738306045532

For User: 0x81153a7A0A3ee058F8Ce28FfF298440726499c7f
From Block: 18965976
Fetching Repay events.
Fetching complete.
Time Elapsed: 0.03124237060546875

For User: 0x81153a7A0A3ee058F8Ce28FfF298440726499c7f
From Block: 18965976
Fetching FlashLoan events.
Fetching complete.
Time Elapsed: 1.3408617973327637

For User

Fetching FlashLoan events.
Fetching complete.
Time Elapsed: 0.850355863571167

For User: 0x8A108776C2447EF7E99973D9c6eF45d83EadC11E
From Block: 19021589
Fetching Withdraw events.
Fetching complete.
Time Elapsed: 0.06328415870666504

For User: 0x8A108776C2447EF7E99973D9c6eF45d83EadC11E
From Block: 19021589
Fetching Borrow events.
Fetching complete.
Time Elapsed: 6.409780025482178

For User: 0x8A108776C2447EF7E99973D9c6eF45d83EadC11E
From Block: 19021589
Fetching Repay events.
Fetching complete.
Time Elapsed: 0.04703187942504883

For User: 0x8A108776C2447EF7E99973D9c6eF45d83EadC11E
From Block: 19021589
Fetching FlashLoan events.
Fetching complete.
Time Elapsed: 0.8431851863861084

For User: 0x052F812f7A66bC7DecbB6580A1a4aA3BB399F7DD
From Block: 19027185
Fetching Withdraw events.
Fetching complete.
Time Elapsed: 0.173109769821167

For User: 0x052F812f7A66bC7DecbB6580A1a4aA3BB399F7DD
From Block: 19027185
Fetching Borrow events.
Fetching complete.
Time Elapsed: 6.970578193664551

For User: 

Fetching Borrow events.
Fetching complete.
Time Elapsed: 4.882312059402466

For User: 0x01dcc7Fd0E8B9f6A05d4eC442504b50111aE678B
From Block: 19069663
Fetching Repay events.
Fetching complete.
Time Elapsed: 0.07907652854919434

For User: 0x01dcc7Fd0E8B9f6A05d4eC442504b50111aE678B
From Block: 19069663
Fetching FlashLoan events.
Fetching complete.
Time Elapsed: 0.5669772624969482

For User: 0x36cc7B13029B5DEe4034745FB4F24034f3F2ffc6
From Block: 19075574
Fetching Withdraw events.
Fetching complete.
Time Elapsed: 0.06007194519042969

For User: 0x36cc7B13029B5DEe4034745FB4F24034f3F2ffc6
From Block: 19075574
Fetching Borrow events.
Fetching complete.
Time Elapsed: 4.757443189620972

For User: 0x36cc7B13029B5DEe4034745FB4F24034f3F2ffc6
From Block: 19075574
Fetching Repay events.
Fetching complete.
Time Elapsed: 0.04523634910583496

For User: 0x36cc7B13029B5DEe4034745FB4F24034f3F2ffc6
From Block: 19075574
Fetching FlashLoan events.
Fetching complete.
Time Elapsed: 0.5071594715118408

For User: 

Fetching FlashLoan events.
Fetching complete.
Time Elapsed: 0.4207155704498291

For User: 0xaeF322446A35705a4D5959FBb3E9E7718533AD43
From Block: 19119942
Fetching Withdraw events.
Fetching complete.
Time Elapsed: 0.02871227264404297

For User: 0xaeF322446A35705a4D5959FBb3E9E7718533AD43
From Block: 19119942
Fetching Borrow events.
Fetching complete.
Time Elapsed: 3.0631918907165527

For User: 0xaeF322446A35705a4D5959FBb3E9E7718533AD43
From Block: 19119942
Fetching Repay events.
Fetching complete.
Time Elapsed: 0.015183210372924805

For User: 0xaeF322446A35705a4D5959FBb3E9E7718533AD43
From Block: 19119942
Fetching FlashLoan events.
Fetching complete.
Time Elapsed: 0.354982852935791

For User: 0x572372831A9d6B2E3ee8fa284505599e6125Fea9
From Block: 19138101
Fetching Withdraw events.
Fetching complete.
Time Elapsed: 0.20665240287780762

For User: 0x572372831A9d6B2E3ee8fa284505599e6125Fea9
From Block: 19138101
Fetching Borrow events.
Fetching complete.
Time Elapsed: 2.382024049758911

For Us

In [11]:
# Dump borrow logs
with open('recentUser_logs.json', 'w') as json_file:
    json.dump(recentUser_logs, json_file, indent=4)
    
# Load borrow logs
with open('recentUser_logs.json', 'r') as json_file:
    recent_logs_from_json = json.load(json_file)
    
recent_logs_from_json

{'0x0418656Fdf3646968489b8e6aF6C25562803c69D': {'Withdraw': {'2023-11-16 10:25:35': [{'Transaction Hash': '0xab8768ff985f88cf20b360016ed65fb7975bdd1fe1cbff8c52d398728427675f',
     'Address': '0x87870Bca3F3fD6335C3F4ce8392D69350B4fA4E2',
     'Block Hash': '0xd7909fe34da5de0b576f7e75bbe34ab66587496806a08c72745bc26de1f04ca0',
     'Block Number': 18583836,
     'Timestamp': '2023-11-16 10:25:35',
     'Reserve': '0xae78736Cd615f374D3085123A210448E74Fc6393',
     'User': '0x0418656Fdf3646968489b8e6aF6C25562803c69D',
     'To': '0x0418656Fdf3646968489b8e6aF6C25562803c69D',
     'Amount': 167090857225061522056}]},
  'Borrow': {'2023-11-15 15:33:23': [{'Transaction Hash': '0x461deeaecf5ef2175715c6c37f6c29af8b183e5c1cc8c9372751f01cf01b0ae5',
     'Address': '0x87870Bca3F3fD6335C3F4ce8392D69350B4fA4E2',
     'Block Hash': '0x5fe58b818e38e4348be1f83bdeb5542f86e4d6fcf6c1ecf1795a1fdba348a027',
     'Block Number': 18578205,
     'Timestamp': '2023-11-15 15:33:23',
     'Reserve': '0xdAC17F958D2e

In [12]:
# Count the number of logs for each user
user_log_counts = {}

for user, events in recent_logs_from_json.items():
    log_count = 0
    for event_name, timestamps in events.items():
        log_count += len(timestamps)  # Assuming each timestamp represents one log
    user_log_counts[user] = log_count

# Sort users by log count in descending order
sorted_users_by_log_count = sorted(user_log_counts.items(), key=lambda x: x[1], reverse=True)

# Display the sorted users and their log counts
for user, count in sorted_users_by_log_count:
    print(f"User {user} has {count} logs.")

User 0xADC0A53095A0af87F3aa29FE0715B5c28016364e has 1722 logs.
User 0x02e7B8511831B1b02d9018215a0f8f500Ea5c6B3 has 1413 logs.
User 0x1aEcea38B8626EEB3748234343cff427268Dd487 has 879 logs.
User 0xa6381631e0634e97E23a80a3c57F9582aa959e16 has 879 logs.
User 0x00000000032962B51589768828ad878876299E14 has 411 logs.
User 0x33333aea097c193e66081E930c33020272b33333 has 373 logs.
User 0xdae0b3CE40F66ec01383B73bc261f50b1585d44b has 46 logs.
User 0xdE13a331adF3B9b6F32017BC63dFf2f61A926a5a has 38 logs.
User 0x9fb1750Da6266a05601855bb62767eBC742707B1 has 32 logs.
User 0x684566C9FFcAC7F6A04C3a9997000d2d58C00824 has 25 logs.
User 0x6F30C82BaE8523C2F78100eB135d4310Ac6EF59B has 22 logs.
User 0xb08856994DD338B0DB1253DCAB0e5F56e27f3985 has 20 logs.
User 0x660Ec6b32C58f682e5d5C619758440e1357bD58C has 20 logs.
User 0xb497070466Dc15FA6420b4781bB0352257146495 has 16 logs.
User 0xee2826453A4Fd5AfeB7ceffeEF3fFA2320081268 has 16 logs.
User 0x194a3c3dEa1c9E90F164109feCC649767dC99870 has 16 logs.
User 0x9Ca458D4E